In [1]:
import tensorflow as tf
from shutil import copyfile,rmtree
import os
from pathlib import Path
import re
import sys
print (tf.__version__)

1.15.0


In [3]:
# Enter your own base folder, where all your other files should be saved to
base_folder = '/home/jovyan'
os.chdir(base_folder)
print(f'base folder is: {base_folder}')

workspace_folder = "my_workspace/"
pretrained_models_folder = "pretrained_models/"
my_models_folder = "my_models/"
my_pipeline = os.path.join(base_folder,workspace_folder,my_models_folder, mymodel, 'pipeline.config')

pretrained_model_name = "awesome_ssd_mobilenet" # can be freely chosen
# Select a pretrained model from the tf1_detection_zoo (link below)
pretrained_model_cnn = "ssd_mobilenet_v1_quantized_300x300_coco14_sync_2018_07_18" 
# Select the corresponding config for your model (link below)
pretrained_model_config = "ssd_mobilenet_v1_quantized_300x300_coco14_sync.config" 

"""
pretrained models:
https://github.com/tensorflow/models/blob/master/research/object_detection/g3doc/tf1_detection_zoo.md
configs:
https://github.com/tensorflow/models/tree/master/research/object_detection/samples/configs
"""

Path(os.path.join(base_folder,workspace_folder,pretrained_models_folder, pretrained_model_name)).mkdir(parents=True, exist_ok=True)
Path(os.path.join(base_folder,workspace_folder,my_models_folder)).mkdir(parents=True, exist_ok=True)

mymodel = 'my_'+pretrained_model_name

base folder is: /home/jovyan


In [6]:
# clone object detection api branch
os.chdir(os.path.join(base_folder, workspace_folder))
if os.path.exists(os.path.join(base_folder, workspace_folder, "models")):
    print("deleting existing object detectionfolder.")
    !rm -rf models
print("cloning object detection api")
!git clone -b r1.13.0 --single-branch https://github.com/tensorflow/models.git
    

deleting existing object detectionfolder.
cloning object detection api
Cloning into 'models'...
remote: Enumerating objects: 21980, done.
remote: Total 21980 (delta 0), reused 0 (delta 0), pack-reused 21980
Receiving objects: 100% (21980/21980), 520.65 MiB | 21.75 MiB/s, done.
Resolving deltas: 100% (13099/13099), done.
Checking out files: 100% (2768/2768), done.


In [7]:
# install dependencies
!pip install pillow
!pip install lxml
!pip install jupyter
!pip install matplotlib
!pip install opencv
!pip install pathlib

You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.
  Using cached lxml-4.6.2-cp37-cp37m-manylinux1_x86_64.whl (5.5 MB)
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.
  Using cached jupyter-1.0.0-py2.py3-none-any.whl (2.7 kB)
     |████████████████████████████████| 119 kB 3.0 MB/s eta 0:00:01
  Using cached jupyter_console-6.2.0-py3-none-any.whl (22 kB)
  Using cached QtPy-1.9.0-py2.py3-none-any.whl (54 kB)
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.
ERROR: Could not find a version that satisfies the requirement opencv (from versions: none)
ERROR: No matching distribution found for opencv
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.
Processing /home/jovyan/.cache/pip/wheels/6e/96

In [8]:
# protoc models research and install object detection api
os.chdir(os.path.join(base_folder, workspace_folder, "models", "research"))
!protoc object_detection/protos/*.proto --python_out=.
!pip install .

Processing /home/jovyan/switch_workspace_edje/models/research
  Created wheel for object-detection: filename=object_detection-0.1-py3-none-any.whl size=800649 sha256=a6d44f65445a4dc89b4a1dd0b915babc344cff143ab140c39e34ae57b0c6da7c
  Stored in directory: /tmp/pip-ephem-wheel-cache-jonjogbi/wheels/f0/ce/51/fe6bb7af81318980504ef3a8b3ad05079daa46680e885e02de
Successfully built object-detection
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


In [9]:
# Set environment variable
env_current = " "
%set_env PYTHONPATH=$env_current:$base_folder/{workspace_folder}models/research
env_current = os.environ['PYTHONPATH']
%set_env PYTHONPATH=$env_current:$base_folder/{workspace_folder}models/research/slim

env: PYTHONPATH=:/home/jovyan/switch_workspace_edje/models/research
env: PYTHONPATH=:/home/jovyan/switch_workspace_edje/models/research:/home/jovyan/switch_workspace_edje/models/research/slim


In [10]:
# Install coco api
os.chdir(os.path.join(base_folder, workspace_folder))
!rm -rf cocoapi
!git clone --depth 1 https://github.com/cocodataset/cocoapi.git
os.chdir(os.path.join("cocoapi", "PythonAPI"))
!make
!cp -r pycocotools $base_folder/{workspace_folder}models/research
os.chdir(os.path.join(base_folder, workspace_folder))
!rm -rf cocoapi


Cloning into 'cocoapi'...
remote: Enumerating objects: 50, done.
remote: Counting objects: 100% (50/50), done.
remote: Compressing objects: 100% (46/46), done.
remote: Total 50 (delta 2), reused 19 (delta 2), pack-reused 0
Unpacking objects: 100% (50/50), done.
python setup.py build_ext --inplace
running build_ext
cythoning pycocotools/_mask.pyx to pycocotools/_mask.c
/opt/conda/lib/python3.7/site-packages/Cython/Compiler/Main.py:369: FutureWarning: Cython directive 'language_level' not set, using 2 for now (Py2). This will change in a later release! File: /home/jovyan/switch_workspace_edje/cocoapi/PythonAPI/pycocotools/_mask.pyx
  tree = Parsing.p_module(s, pxd, full_module_name)
building 'pycocotools._mask' extension
creating build
creating build/common
creating build/temp.linux-x86_64-3.7
creating build/temp.linux-x86_64-3.7/pycocotools
gcc -pthread -B /opt/conda/compiler_compat -Wl,--sysroot=/ -Wsign-compare -DNDEBUG -g -fwrapv -O3 -Wall -Wstrict-prototypes -fPIC -I/opt/conda/lib/p

In [68]:
# Gettings Pictures from my own git. You can also use these pictures as a reference or to get something to train quickly
os.chdir(os.path.join(base_folder,workspace_folder))
!rm -rf switch_example_input
!git lfs install
!git clone -b augmented --single-branch --depth 1 https://github.com/Frooob/switch_example_input.git

Error: Failed to call git rev-parse --git-dir --show-toplevel: "fatal: not a git repository (or any parent up to mount point /home)\nStopping at filesystem boundary (GIT_DISCOVERY_ACROSS_FILESYSTEM not set).\n"
Git LFS initialized.
Cloning into 'switch_example_input'...
remote: Enumerating objects: 184, done.
remote: Counting objects: 100% (184/184), done.
remote: Compressing objects: 100% (184/184), done.
remote: Total 184 (delta 0), reused 181 (delta 0), pack-reused 0
Receiving objects: 100% (184/184), 26.17 KiB | 1.87 MiB/s, done.
Filtering content: 100% (178/178), 254.91 MiB | 20.95 MiB/s, done.


In [80]:
os.chdir(os.path.join(base_folder,workspace_folder, "switch_example_input", "myTfrecords"))
!du -h
!ls -l -h

4.0K	./.ipynb_checkpoints
116M	.
total 116M
-rw-r--r-- 1 jovyan users 31M Jan 15 21:49 evaluation.record
-rw-r--r-- 1 jovyan users  93 Jan 15 21:49 label_map.pbtxt
-rw-r--r-- 1 jovyan users 23M Jan 15 21:49 test.record
-rw-r--r-- 1 jovyan users 63M Jan 16 08:26 train.record


In [4]:
train_record_fname = os.path.join(base_folder, workspace_folder, 'switch_example_input',"myTfrecords", "train.record")
valid_record_fname  =os.path.join(base_folder, workspace_folder,'switch_example_input',"myTfrecords", "test.record")
test_record_fname =os.path.join(base_folder, workspace_folder, 'switch_example_input',"myTfrecords", "evaluation.record")
label_map_pbtxt_fname =os.path.join(base_folder, workspace_folder,'switch_example_input',"myTfrecords","label_map.pbtxt")
print(f'all data fetched correctly: {all([os.path.exists(train_record_fname),os.path.exists(valid_record_fname),os.path.exists(test_record_fname),os.path.exists(label_map_pbtxt_fname)])}')

all data fetched correctly: True


In [82]:
# Download the pretrained model
os.chdir(os.path.join(base_folder,workspace_folder, pretrained_models_folder, pretrained_model_name))
!wget https://raw.githubusercontent.com/tensorflow/models/master/research/object_detection/samples/configs/{pretrained_model_config}
!wget http://download.tensorflow.org/models/object_detection/{pretrained_model_cnn}.tar.gz

!tar -xzvf {pretrained_model_cnn}.tar.gz
!rm {pretrained_model_cnn}.tar.gz

--2021-01-16 08:26:48--  https://raw.githubusercontent.com/tensorflow/models/master/research/object_detection/samples/configs/ssd_mobilenet_v1_quantized_300x300_coco14_sync.config
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 151.101.112.133
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|151.101.112.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4505 (4.4K) [text/plain]
Saving to: ‘ssd_mobilenet_v1_quantized_300x300_coco14_sync.config’

ssd_mobilenet_v1_qu 100%[===================>]   4.40K  --.-KB/s    in 0s      

2021-01-16 08:26:48 (57.8 MB/s) - ‘ssd_mobilenet_v1_quantized_300x300_coco14_sync.config’ saved [4505/4505]

--2021-01-16 08:26:49--  http://download.tensorflow.org/models/object_detection/ssd_mobilenet_v1_quantized_300x300_coco14_sync_2018_07_18.tar.gz
Resolving download.tensorflow.org (download.tensorflow.org)... 172.217.19.80
Connecting to download.tensorflow.org (download.tensorflow.org)|172.217.19

In [83]:
num_classes = 2
batch_size = 12
num_train_images = 4040
number_of_steps = 70000 

os.chdir(os.path.join(base_folder, workspace_folder, my_models_folder))

#rmtree(mymodel,ignore_errors=True)
os.makedirs(mymodel, exist_ok = True)

if os.path.exists(my_pipeline): os.remove(my_pipeline)

copyfile(os.path.join(base_folder, workspace_folder, pretrained_models_folder, pretrained_model_name, pretrained_model_config), my_pipeline)

#checkpoint muss noch gesetzt werden!
fine_tune_checkpoint = os.path.join(base_folder, workspace_folder, pretrained_models_folder, pretrained_model_name, pretrained_model_cnn, 'model.ckpt')
print(f"finetunecheckpoint: {fine_tune_checkpoint}")


with open(my_pipeline) as f:
    s = f.read()
with open(my_pipeline, 'w') as f:
    # fine_tune_checkpoint
    s = re.sub('num_classes: \d*', f'num_classes: {num_classes}',s)
    s = re.sub('batch_size: \d*', f'batch_size: {batch_size}',s)
    s = re.sub('total_steps: \d*', f'total_steps: {number_of_steps}',s)
    s = re.sub('num_steps: \d*', f'num_steps: {number_of_steps}',s)
    s = re.sub('fine_tune_checkpoint: ".*?"', f'fine_tune_checkpoint: "{fine_tune_checkpoint}"',s)

    # tfrecord files train and test.
    s = re.sub(
        'input_path: "PATH_TO_BE_CONFIGURED.*', f'input_path: "{train_record_fname}"', s,1)
    s = re.sub(
        'input_path: "PATH_TO_BE_CONFIGURED.*', f'input_path: "{valid_record_fname}"', s,1)

    # label_map_path
    s = re.sub(
        'label_map_path: ".*?"', f'label_map_path: "{label_map_pbtxt_fname}"', s)

    # enable coco evaluation
    s = re.sub(
        '# metrics_set: ', 'metrics_set: ', s)
    
    # 
    s = re.sub('num_examples: \d*', f'num_examples: {num_train_images}\n  max_evals: 10',s)
    
    s = re.sub("""  data_augmentation_options {
    random_horizontal_flip {
    }
  }""","", s)
    s = re.sub("""  data_augmentation_options {
    ssd_random_crop {
    }
  }""","", s)

    
    f.write(s)

os.chdir(os.path.join(base_folder, workspace_folder, my_models_folder, mymodel))
!cat pipeline.config

finetunecheckpoint: /home/jovyan/switch_workspace_edje/pretrained_models/ssd_mobilenet_v1_300x300_more_raspictures_train_augmented_pipeline2/ssd_mobilenet_v1_quantized_300x300_coco14_sync_2018_07_18/model.ckpt
# SSD with Mobilenet v1 with quantized training.
# Trained on COCO, initialized from Imagenet classification checkpoint

# Achieves 18.2 mAP on coco14 minival dataset.

# This config is TPU compatible

model {
  ssd {
    inplace_batchnorm_update: true
    freeze_batchnorm: false
    num_classes: 2
    box_coder {
      faster_rcnn_box_coder {
        y_scale: 10.0
        x_scale: 10.0
        height_scale: 5.0
        width_scale: 5.0
      }
    }
    matcher {
      argmax_matcher {
        matched_threshold: 0.5
        unmatched_threshold: 0.5
        ignore_thresholds: false
        negatives_lower_than_unmatched: true
        force_match_for_each_row: true
        use_matmul_gather: true
      }
    }
    similarity_calculator {
      iou_similarity {
      }
    }
    en

In [84]:
os.chdir(os.path.join(base_folder, workspace_folder))
copyfile(os.path.join(base_folder, workspace_folder, "models", "research", 'object_detection','model_main.py'), './model_main.py')

'./model_main.py'

In [85]:
!python model_main.py \
--alsologtostderr \
--model_dir=$base_folder/{workspace_folder}{my_models_folder}{mymodel} \
--pipeline_config_path=$base_folder/{workspace_folder}{my_models_folder}{mymodel}/pipeline.config

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.





W0116 08:27:36.991208 139732196558656 module_wrapper.py:139] From /home/jovyan/switch_workspace_edje/models/research/object_detection/utils/config_util.py:94: The name tf.gfile.GFile is deprecated. Please use tf.io.gfile.GFile instead.


W0116 08:27:36.994109 139732196558656 module_wrapper.py:139] From /home/jovyan/switch_workspace_edje/models/research/object_detection/model_lib.py:573: The name tf.logging.warning is deprecated. Please use tf.compat.v1.logging.warning instead.

W0116 08:27:36.994212 139732196558656 model_lib.py:574] Forced number of epochs for all eval validations to be 1.

W0116 08:27:36.994306 139732196558

In [90]:
mymodel

'my_ssd_mobilenet_v1_300x300_more_raspictures_train_augmented_pipeline2'

In [91]:
os.chdir(os.path.join(base_folder, workspace_folder, my_models_folder))

my_evaluation_pipeline = os.path.join(base_folder,workspace_folder,my_models_folder, mymodel, 'evaluation_pipeline.config')
if os.path.exists(my_evaluation_pipeline): os.remove(my_evaluation_pipeline)

copyfile(my_pipeline, my_evaluation_pipeline)

with open(my_evaluation_pipeline) as f:
    s = f.read()
with open(my_evaluation_pipeline, 'w') as f:
    s = re.sub(
        f'input_path: "{train_record_fname}"', f'input_path: "{test_record_fname}"', s,1)
    s = re.sub(
        f'input_path: "{valid_record_fname}"', f'input_path: "{test_record_fname}"', s,1)
    f.write(s)

os.chdir(os.path.join(base_folder, workspace_folder, my_models_folder, mymodel))
!cat evaluation_pipeline.config

# SSD with Mobilenet v1 with quantized training.
# Trained on COCO, initialized from Imagenet classification checkpoint

# Achieves 18.2 mAP on coco14 minival dataset.

# This config is TPU compatible

model {
  ssd {
    inplace_batchnorm_update: true
    freeze_batchnorm: false
    num_classes: 2
    box_coder {
      faster_rcnn_box_coder {
        y_scale: 10.0
        x_scale: 10.0
        height_scale: 5.0
        width_scale: 5.0
      }
    }
    matcher {
      argmax_matcher {
        matched_threshold: 0.5
        unmatched_threshold: 0.5
        ignore_thresholds: false
        negatives_lower_than_unmatched: true
        force_match_for_each_row: true
        use_matmul_gather: true
      }
    }
    similarity_calculator {
      iou_similarity {
      }
    }
    encode_background_as_zeros: true
    anchor_generator {
      ssd_anchor_generator {
        num_layers: 6
        min_scale: 0.2
        max_scale: 0.95
        aspect_ratios: 1.0
        aspect_ratios: 2.0
    

In [15]:
os.chdir(os.path.join(base_folder, workspace_folder))
!python model_main.py \
    --alsologtostderr \
    --checkpoint_dir=$base_folder/{workspace_folder}{my_models_folder}{mymodel} \
    --model_dir=$base_folder/{workspace_folder}{my_models_folder}{mymodel} \
    --pipeline_config_path=$base_folder/{workspace_folder}{my_models_folder}{mymodel}/evaluation_pipeline.config

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.





W0129 14:27:59.203381 139637726324544 module_wrapper.py:139] From /home/jovyan/switch_workspace_edje/models/research/object_detection/utils/config_util.py:94: The name tf.gfile.GFile is deprecated. Please use tf.io.gfile.GFile instead.


W0129 14:27:59.206343 139637726324544 module_wrapper.py:139] From /home/jovyan/switch_workspace_edje/models/research/object_detection/model_lib.py:573: The name tf.logging.warning is deprecated. Please use tf.compat.v1.logging.warning instead.

W0129 14:27:59.206470 139637726324544 model_lib.py:574] Forced number of epochs for all eval validations to be 1.

W0129 14:27:59.206557 139637726324

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [16]:
os.chdir(os.path.join(base_folder, workspace_folder))
!python model_main.py \
    --alsologtostderr \
    --checkpoint_dir=$base_folder/{workspace_folder}{my_models_folder}{mymodel} \
    --model_dir=$base_folder/{workspace_folder}{my_models_folder}{mymodel} \
    --pipeline_config_path=$base_folder/{workspace_folder}{my_models_folder}{mymodel}/pipeline.config

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.





W0129 14:28:30.449806 140286928254784 module_wrapper.py:139] From /home/jovyan/switch_workspace_edje/models/research/object_detection/utils/config_util.py:94: The name tf.gfile.GFile is deprecated. Please use tf.io.gfile.GFile instead.


W0129 14:28:30.452510 140286928254784 module_wrapper.py:139] From /home/jovyan/switch_workspace_edje/models/research/object_detection/model_lib.py:573: The name tf.logging.warning is deprecated. Please use tf.compat.v1.logging.warning instead.

W0129 14:28:30.452634 140286928254784 model_lib.py:574] Forced number of epochs for all eval validations to be 1.

W0129 14:28:30.452719 140286928254

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

